In [ ]:
%%capture
!pip -q install git+https://github.com/huggingface/transformers
!pip install -q datasets loralib sentencepiece
!pip -q install bitsandbytes accelerate
!pip -q install langchain
!pip install faiss-gpu
!pip install --upgrade --quiet  langchain-community chromadb bs4 qdrant-client
!pip install langchainhub

In [ ]:
%%capture
!pip -q install git+https://github.com/huggingface/transformers
!pip install -q datasets
!pip -q install langchain
!pip install einops
!pip install faiss-gpu
!pip install --upgrade --quiet  langchain-community chromadb bs4 qdrant-client
!pip install langchainhub
!pip install sentence-transformers
!pip install tqdm

In [ ]:
%%capture
!pip install rouge_score nltk datasets

In [ ]:
%%capture
!pip install bert_score

In [ ]:
#!pip install git+https://github.com/sleighton2022/datasci266-final-project.git
!wget https://raw.githubusercontent.com/sleighton2022/datasci266-final-project/main/summary_utils.py
from summary_utils import SummaryEvaluator, DatasetManager, SummaryModel

--2024-07-22 05:56:05--  https://raw.githubusercontent.com/sleighton2022/datasci266-final-project/main/summary_utils.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 11185 (11K) [text/plain]
Saving to: ‘summary_utils.py.4’

summary_utils.py.4  100%[===================>]  10.92K  --.-KB/s    in 0.001s  

2024-07-22 05:56:05 (13.3 MB/s) - ‘summary_utils.py.4’ saved [11185/11185]



In [ ]:
import os
import torch
from datasets import load_dataset
from tqdm import tqdm
from langchain.schema import Document
from langchain.vectorstores import FAISS
from langchain.docstore.in_memory import InMemoryDocstore
from langchain import PromptTemplate, LLMChain
from langchain_core.prompts import ChatPromptTemplate
from langchain.embeddings import OpenAIEmbeddings
from langchain.llms import HuggingFacePipeline
from langchain_community.embeddings import HuggingFaceEmbeddings
from langchain_core.runnables import RunnablePassthrough
from langchain.text_splitter import RecursiveCharacterTextSplitter
from transformers import AutoTokenizer , AutoModelForCausalLM
from transformers import pipeline, BitsAndBytesConfig

In [ ]:
summary_evaluator = SummaryEvaluator()

In [ ]:
# Load the XSum dataset
dataset = load_dataset("xsum")

# Initialize the Embeddings
embeddings = HuggingFaceEmbeddings(model_name="all-MiniLM-L6-v2")

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(


In [ ]:
%%capture

quantization_config = BitsAndBytesConfig(load_in_4bit=True,
                                         llm_int4_enable_fp32_cpu_offload=True)


llm_mistral_model = AutoModelForCausalLM.from_pretrained(
    "mistralai/Mistral-7B-Instruct-v0.1",
    torch_dtype=torch.float32,
    device_map='auto',
    quantization_config=quantization_config
)

llm_mistral_tokenizer = AutoTokenizer.from_pretrained("mistralai/Mistral-7B-Instruct-v0.1")

Unused kwargs: ['llm_int4_enable_fp32_cpu_offload']. These kwargs are not used in <class 'transformers.utils.quantization_config.BitsAndBytesConfig'>.


In [ ]:
mistral_pipe = pipeline(
    "text-generation",
    model=llm_mistral_model,
    tokenizer=llm_mistral_tokenizer,
    max_length=1000,
    temperature=0.6,
    top_p=0.95,
    do_sample=True,
    repetition_penalty=1.2
)
mistral_pipe.model.config.pad_token_id = mistral_pipe.model.config.eos_token_id


In [ ]:
mistral_llm_lc = HuggingFacePipeline(pipeline=mistral_pipe)

/usr/local/lib/python3.10/dist-packages/langchain_core/_api/deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFacePipeline` was deprecated in LangChain 0.0.37 and will be removed in 0.3. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFacePipeline`.
  warn_deprecated(


In [ ]:
class RAG_Summarization_Model:
  def __init__(self, chunk_size=200, chunk_overlap=50):
    self.vector_store = None
    self.rag_chain = None
    self.chunk_size = chunk_size
    self.chunk_overlap = chunk_overlap

  def fit(self, dataset):
    # Function to split documents and include metadata
    def create_documents_with_metadata(dataset, chunk_size=200, chunk_overlap=50):
      # Initialize the text splitter
      text_splitter = RecursiveCharacterTextSplitter(
          chunk_size=chunk_size,  # Adjust based on your needs
          chunk_overlap=chunk_overlap  # Adjust based on your needs
      )
      documents = []
      for example in dataset:
          text = example['document']
          # Split the text into chunks while including metadata
          chunks = text_splitter.split_text(text)
          for chunk in chunks:
              documents.append(Document(page_content=chunk, metadata={"id": example['id']}))
      return documents
    # Create documents with metadata
    documents = create_documents_with_metadata(dataset, self.chunk_size, self.chunk_overlap)
    # Create a FAISS vector store
    self.vector_store = FAISS.from_documents(documents, embeddings)

    rag_template = """[INST] Give me a short one-sentence summarization with the following context: {context}[/INST]"""

    rag_prompt = ChatPromptTemplate.from_template(rag_template)

    self.rag_chain = (
        {"context": lambda inputs: self.format_docs(self.query_vector_store(inputs['query'], inputs['id'], k=inputs['k'], fetch_k=inputs['fetch_k'])),
        "question": RunnablePassthrough()}
        | rag_prompt
        | mistral_llm_lc
    )

  def query_vector_store(self, query_text, summary_id, k=3, fetch_k=20):
    # Embed the query text
    query_vector = embeddings.embed_query(query_text)
    # Search the vector store
    docs = self.vector_store.similarity_search_by_vector(query_vector, filter=dict(summary_id=summary_id), k=k, fetch_k=fetch_k)
    return docs

  def format_docs(self, docs):
      return "\n\n".join(doc.page_content for doc in docs)

  def predict(self, dataset, k, fetch_k):
    results = []
    i = 1
    for example in tqdm(dataset):
        print(i)
        text = example['document']
        sentences = re.split(r'[.?!]\s+', text)
        example_query = sentences[-1]
        summary_w_prompt = self.rag_chain.invoke({"query": example_query, "id": example['id'], "k":k, 'fetch_k':fetch_k})
        summary = summary_w_prompt.split("[/INST] ",1)[1]
        results.append(summary)
        i += 1
    return results

In [ ]:
validation_dataset = dataset['validation'].take(1500)

In [ ]:
references = [example['summary'] for example in validation_dataset]

In [ ]:
import re

In [ ]:
rag_model = RAG_Summarization_Model(chunk_size=200, chunk_overlap=50)
rag_model.fit(validation_dataset)
predictions1 = rag_model.predict(validation_dataset, k=3, fetch_k=20)
predictions2 = rag_model.predict(validation_dataset, k=5, fetch_k=20)
predictions3 = rag_model.predict(validation_dataset, k=3, fetch_k=10)
predictions4 = rag_model.predict(validation_dataset, k=5, fetch_k=10)

  0%|          | 0/1500 [00:00<?, ?it/s]Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.
Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1


  0%|          | 1/1500 [00:03<1:34:33,  3.78s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


2


  0%|          | 2/1500 [00:08<1:43:52,  4.16s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


...

100%|█████████▉| 1498/1500 [56:19<00:04,  2.30s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1499


100%|█████████▉| 1499/1500 [56:21<00:02,  2.48s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1500


100%|██████████| 1500/1500 [56:23<00:00,  2.26s/it]


In [ ]:
print("chunk_size=200, chunk_overlap=50")
print("k=3, fetch_k=20")
summary_evaluator.evaluate(references, predictions1)
print("k=5, fetch_k=20")
summary_evaluator.evaluate(references, predictions2)
print("k=3, fetch_k=10")
summary_evaluator.evaluate(references, predictions3)
print("k=5, fetch_k=10")
summary_evaluator.evaluate(references, predictions4)

chunk_size=200, chunk_overlap=50
k=3, fetch_k=20


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

...

A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08495294029540916, 'rouge2': 0.0015137368753309927, 'rougeL': 0.06959077669192955}
Average BLEU score: 0.00902484905965987
Average BERTScore (F1): 0.3536604046821594
Average Vector Similarity (Cosine): 0.00668466929346323
k=5, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08454707534777811, 'rouge2': 0.0017472173123979358, 'rougeL': 0.06946283091644895}
Average BLEU score: 0.008640339028118463
Average BERTScore (F1): 0.35265910625457764
Average Vector Similarity (Cosine): 0.0087346900254488


({'rouge1': 0.08454707534777811,
  'rouge2': 0.0017472173123979358,
  'rougeL': 0.06946283091644895},
 0.008640339028118463,
 0.35265910625457764,
 0.0087346900254488)

In [ ]:
rag_model = RAG_Summarization_Model(chunk_size=100, chunk_overlap=50)
rag_model.fit(validation_dataset)
predictions1 = rag_model.predict(validation_dataset, k=3, fetch_k=20)
predictions2 = rag_model.predict(validation_dataset, k=5, fetch_k=20)
predictions3 = rag_model.predict(validation_dataset, k=3, fetch_k=10)
predictions4 = rag_model.predict(validation_dataset, k=5, fetch_k=10)

  0%|          | 0/1500 [00:00<?, ?it/s]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1


  0%|          | 1/1500 [00:02<50:42,  2.03s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


2


  0%|          | 2/1500 [00:04<56:11,  2.25s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


...

100%|█████████▉| 1498/1500 [57:29<00:04,  2.46s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1499


100%|█████████▉| 1499/1500 [57:31<00:02,  2.26s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1500


100%|██████████| 1500/1500 [57:33<00:00,  2.30s/it]


In [ ]:
print("chunk_size=100, chunk_overlap=50")
print("k=3, fetch_k=20")
summary_evaluator.evaluate(references, predictions1)
print("k=5, fetch_k=20")
summary_evaluator.evaluate(references, predictions2)
print("k=3, fetch_k=10")
summary_evaluator.evaluate(references, predictions3)
print("k=5, fetch_k=10")
summary_evaluator.evaluate(references, predictions4)

chunk_size=100, chunk_overlap=50
k=3, fetch_k=20


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08624106295894737, 'rouge2': 0.0017955333674640286, 'rougeL': 0.07106372890478231}
Average BLEU score: 0.008989641250875107
Average BERTScore (F1): 0.3531554341316223
Average Vector Similarity (Cosine): 0.006400910671800375
k=5, fetch_k=20


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08429663594520069, 'rouge2': 0.0015394712331089518, 'rougeL': 0.06966113998618341}
Average BLEU score: 0.00898260287785445
Average BERTScore (F1): 0.35471948981285095
Average Vector Similarity (Cosine): 0.009176956489682198
k=3, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08561376473296407, 'rouge2': 0.0015197668252355742, 'rougeL': 0.07031452915503739}
Average BLEU score: 0.00876386028087632
Average BERTScore (F1): 0.3548140525817871
Average Vector Similarity (Cosine): 0.010474598035216331
k=5, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08404489531833559, 'rouge2': 0.0017515300627243785, 'rougeL': 0.06927375672087033}
Average BLEU score: 0.008940948535806209
Average BERTScore (F1): 0.3525150418281555
Average Vector Similarity (Cosine): 0.00806840043514967


({'rouge1': 0.08404489531833559,
  'rouge2': 0.0017515300627243785,
  'rougeL': 0.06927375672087033},
 0.008940948535806209,
 0.3525150418281555,
 0.00806840043514967)

In [ ]:
rag_model = RAG_Summarization_Model(chunk_size=200, chunk_overlap=0)
rag_model.fit(validation_dataset)
predictions1 = rag_model.predict(validation_dataset, k=3, fetch_k=20)
predictions2 = rag_model.predict(validation_dataset, k=5, fetch_k=20)
predictions3 = rag_model.predict(validation_dataset, k=3, fetch_k=10)
predictions4 = rag_model.predict(validation_dataset, k=5, fetch_k=10)

  0%|          | 0/1500 [00:00<?, ?it/s]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1


  0%|          | 1/1500 [00:02<52:10,  2.09s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


2


  0%|          | 2/1500 [00:03<42:29,  1.70s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


...

100%|█████████▉| 1498/1500 [56:57<00:04,  2.31s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1499


100%|█████████▉| 1499/1500 [56:59<00:02,  2.34s/it]Setting `pad_token_id` to `eos_token_id`:2 for open-end generation.


1500


100%|██████████| 1500/1500 [57:02<00:00,  2.28s/it]


In [ ]:
print("chunk_size=200, chunk_overlap=0")
print("k=3, fetch_k=20")
summary_evaluator.evaluate(references, predictions1)
print("k=5, fetch_k=20")
summary_evaluator.evaluate(references, predictions2)
print("k=3, fetch_k=10")
summary_evaluator.evaluate(references, predictions3)
print("k=5, fetch_k=10")
summary_evaluator.evaluate(references, predictions4)

chunk_size=200, chunk_overlap=0
k=3, fetch_k=20


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08703645083486646, 'rouge2': 0.0016785650333188693, 'rougeL': 0.0710176100412728}
Average BLEU score: 0.009266019911861656
Average BERTScore (F1): 0.3540852963924408
Average Vector Similarity (Cosine): 0.007763117551803589
k=5, fetch_k=20


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08631300462907117, 'rouge2': 0.0018525617656889128, 'rougeL': 0.07085825759773624}
Average BLEU score: 0.009272066654419698
Average BERTScore (F1): 0.35465681552886963
Average Vector Similarity (Cosine): 0.0065846857614815235
k=3, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08319764992741643, 'rouge2': 0.0012296652690189373, 'rougeL': 0.06768225254043429}
Average BLEU score: 0.008808466320607248
Average BERTScore (F1): 0.35140469670295715
Average Vector Similarity (Cosine): 0.007623785641044378
k=5, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08704028557503268, 'rouge2': 0.0020592622132696603, 'rougeL': 0.07122494061309276}
Average BLEU score: 0.009061443419063394
Average BERTScore (F1): 0.35317927598953247
Average Vector Similarity (Cosine): 0.009540813975036144


({'rouge1': 0.08704028557503268,
  'rouge2': 0.0020592622132696603,
  'rougeL': 0.07122494061309276},
 0.009061443419063394,
 0.35317927598953247,
 0.009540813975036144)

In [ ]:
rag_model = RAG_Summarization_Model(chunk_size=150, chunk_overlap=0)
rag_model.fit(validation_dataset)
predictions1 = rag_model.predict(validation_dataset, k=3, fetch_k=20)
predictions2 = rag_model.predict(validation_dataset, k=5, fetch_k=20)
predictions3 = rag_model.predict(validation_dataset, k=3, fetch_k=10)
predictions4 = rag_model.predict(validation_dataset, k=5, fetch_k=10)

In [ ]:
print("chunk_size=150, chunk_overlap=0")
print("k=3, fetch_k=20")
summary_evaluator.evaluate(references, predictions1)
print("k=5, fetch_k=20")
summary_evaluator.evaluate(references, predictions2)
print("k=3, fetch_k=10")
summary_evaluator.evaluate(references, predictions3)
print("k=5, fetch_k=10")
summary_evaluator.evaluate(references, predictions4)

chunk_size=150, chunk_overlap=0
k=3, fetch_k=20


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08630339043766637, 'rouge2': 0.0016597738599805506, 'rougeL': 0.07125006914368992}
Average BLEU score: 0.009232311138437456
Average BERTScore (F1): 0.35462474822998047
Average Vector Similarity (Cosine): 0.007269714493304491
k=5, fetch_k=20


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08578919794282214, 'rouge2': 0.0012058991359987824, 'rougeL': 0.07011065428800775}
Average BLEU score: 0.009127536504374333
Average BERTScore (F1): 0.3538339138031006
Average Vector Similarity (Cosine): 0.009754115715622902
k=3, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08677765248154456, 'rouge2': 0.0015207924833682987, 'rougeL': 0.07095107846372545}
Average BLEU score: 0.009096514370849676
Average BERTScore (F1): 0.35479971766471863
Average Vector Similarity (Cosine): 0.010560214519500732
k=5, fetch_k=10


A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Please use a different name to suppress this warning.
A parameter name that contains `beta` will be renamed internally to `bias`. Please use a different name to suppress this warning.
A parameter name that contains `gamma` will be renamed internally to `weight`. Pl

Average ROUGE scores: {'rouge1': 0.08666281276712846, 'rouge2': 0.0015536252090899427, 'rougeL': 0.07125000342498919}
Average BLEU score: 0.009131324036743433
Average BERTScore (F1): 0.35369735956192017
Average Vector Similarity (Cosine): 0.008643550798296928


({'rouge1': 0.08666281276712846,
  'rouge2': 0.0015536252090899427,
  'rougeL': 0.07125000342498919},
 0.009131324036743433,
 0.35369735956192017,
 0.008643550798296928)